In [1]:
TRAIN = '/kaggle/input/sign-language-dataset'

In [2]:
import pandas as pd

df = pd.read_csv(filepath_or_buffer='/kaggle/input/sign-language-dataset/annotations.csv')
df.head()

filename  width  height class  xmin  ymin  xmax  ymax
0  image_000000.jpg    512     512     A    88     0   283   165
1  image_000000.jpg    512     512     X    11    34   223   231
2  image_000001.jpg    512     512     Q   190   193   362   364
3  image_000002.jpg    512     512     O   237     0   404   133
4  image_000003.jpg    512     512     K    54   210   197   343

In [3]:
import torch
import torchvision.models as models
import torchvision.transforms as transforms
import numpy as np


DEVICE = torch.device('cpu')
OUTPUT_SIZE = 2048

model = models.resnext50_32x4d(weights=models.ResNeXt50_32X4D_Weights.IMAGENET1K_V2)

extraction_layer = model._modules.get('avgpool')
model.to(DEVICE)
model.eval()

scaler = transforms.Resize((224, 224))
normalize = transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
to_tensor = transforms.ToTensor()

def get_vec(arg, model, extraction_layer):
    image = normalize(to_tensor(scaler(arg))).unsqueeze(0).to(DEVICE)
    result = torch.zeros(1, OUTPUT_SIZE, 1, 1)
    def copy_data(m, i, o):
        result.copy_(o.data)
    hooked = extraction_layer.register_forward_hook(copy_data)
    with torch.no_grad():
        model(image)
    hooked.remove()
    return result

Downloading: "https://download.pytorch.org/models/resnext50_32x4d-1a0047aa.pth" to /root/.cache/torch/hub/checkpoints/resnext50_32x4d-1a0047aa.pth
100%|██████████| 95.8M/95.8M [00:00<00:00, 175MB/s]


In [4]:
import arrow
import base64
import pandas as pd
from glob import iglob
from io import BytesIO
from os.path import basename
from PIL import Image

THUMBNAIL_SIZE = (64, 64)

def embed(model, filename: str):
    with Image.open(fp=filename, mode='r') as image:
        return get_vec(arg=image.convert('RGB'), model=model, extraction_layer=extraction_layer).numpy().reshape(OUTPUT_SIZE,)


# https://stackoverflow.com/a/952952
def flatten(arg):
    return [x for xs in arg for x in xs]

def png(filename: str) -> str:
    with Image.open(fp=filename, mode='r') as image:
        buffer = BytesIO()
        # our images are pretty big; let's shrink the hover images to thumbnail size
        image.resize(size=THUMBNAIL_SIZE).convert('RGB').save(buffer, format='png')
        return 'data:image/png;base64,' + base64.b64encode(buffer.getvalue()).decode()

def get_picture_from_glob(arg: str, tag: str,) -> list:
    time_get = arrow.now()
    result = [pd.Series(data=[tag, basename(input_file), embed(model=model, filename=input_file), png(filename=input_file)],
                        index=['tag', 'name', 'value', 'png'] )
        for index, input_file in enumerate(list(iglob(pathname=arg))) if input_file.endswith('.jpg')]
    print('encoded {} rows of {}  in {}'.format(len(result), tag, arrow.now() - time_get))
    return result

time_start = arrow.now()
train_dict = {basename(folder) : folder + '/*.*' for folder in iglob(TRAIN + '/*') }
train_df = pd.DataFrame(data=flatten(arg=[get_picture_from_glob(arg=value, tag=key) for key, value in train_dict.items()]))
print('done in {}'.format(arrow.now() - time_start))

encoded 0 rows of generation_script.txt  in 0:00:00.000924
encoded 0 rows of README.txt  in 0:00:00.000941
encoded 1000 rows of images  in 0:02:32.174248
encoded 0 rows of annotations.csv  in 0:00:00.000851
done in 0:02:32.245985


In [5]:
train_df.columns

Index(['tag', 'name', 'value', 'png'], dtype='object')

In [6]:
train_df = train_df.merge(right=df, left_on='name', right_on='filename')

In [7]:
train_df.columns

Index(['tag', 'name', 'value', 'png', 'filename', 'width', 'height', 'class',
       'xmin', 'ymin', 'xmax', 'ymax'],
      dtype='object')

In [8]:
from sklearn.manifold import TSNE

train_reducer = TSNE(random_state=2025, verbose=True, n_jobs=1, perplexity=20.0, init='pca')
train_df[['x', 'y']] = train_reducer.fit_transform(X=train_df['value'].apply(func=pd.Series))


[t-SNE] Computing 61 nearest neighbors...
[t-SNE] Indexed 1058 samples in 0.006s...
[t-SNE] Computed neighbors for 1058 samples in 0.274s...
[t-SNE] Computed conditional probabilities for sample 1000 / 1058
[t-SNE] Computed conditional probabilities for sample 1058 / 1058
[t-SNE] Mean sigma: 2.401473
[t-SNE] KL divergence after 250 iterations with early exaggeration: 68.273682
[t-SNE] KL divergence after 1000 iterations: 1.061030


In [9]:
from bokeh.models import ColumnDataSource
from bokeh.models import HoverTool

from bokeh.plotting import figure
from bokeh.plotting import output_notebook
from bokeh.plotting import show
from bokeh.palettes import Turbo256
from bokeh.transform import factor_cmap

output_notebook()

datasource = ColumnDataSource(train_df[['png', 'class', 'x', 'y']])
factor_count = max(train_df['class'].nunique(), 3)
indices = np.linspace(0, len(Turbo256)-1, factor_count, dtype=int)
palette = [Turbo256[index] for index in indices]
mapper = factor_cmap(field_name = 'class', palette=palette, factors=train_df['class'].unique().tolist(), start=0, end=factor_count-1, )

plot_figure = figure(title='TSNE projection: sign language', width=1000, height=800, tools=('pan, wheel_zoom, reset'))

plot_figure.add_tools(HoverTool(tooltips="""
<div>
    <div>
        <img src='@png' style='float: left; margin: 5px 5px 5px 5px'/>
    </div>
    <div>
        <span style='font-size: 18px'>@class</span>
    </div>
</div>
"""))

plot_figure.scatter(x='x', y='y', source=datasource, line_alpha=0.6, fill_alpha=0.6, size=8, color=mapper)
show(plot_figure)

Loading BokehJS ...

In [10]:
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score
from sklearn.metrics import classification_report
from sklearn.metrics import f1_score
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(train_df['value'].apply(pd.Series), train_df['class'], test_size=0.25, random_state=2025, stratify=train_df['class'])
logreg = LogisticRegression(max_iter=1000, tol=1e-12).fit(X_train, y_train)
print('model fit in {} iterations'.format(logreg.n_iter_[0]))
print('accuracy: {:5.4f}'.format(accuracy_score(y_true=y_test, y_pred=logreg.predict(X=X_test))))
print('f1: {:5.4f}'.format(f1_score(average='weighted', y_true=y_test, y_pred=logreg.predict(X=X_test))))
print(classification_report(y_true=y_test, y_pred=logreg.predict(X=X_test)))

model fit in 776 iterations
accuracy: 0.0302
f1: 0.0279
              precision    recall  f1-score   support

           A       0.00      0.00      0.00        10
           B       0.00      0.00      0.00         8
           C       0.05      0.09      0.06        11
           D       0.00      0.00      0.00        11
           E       0.00      0.00      0.00        10
           F       0.00      0.00      0.00        12
           G       0.00      0.00      0.00        10
           H       0.08      0.14      0.11        14
           I       0.00      0.00      0.00        12
           J       0.00      0.00      0.00        10
           K       0.00      0.00      0.00        11
           L       0.00      0.00      0.00        10
           M       0.33      0.12      0.18         8
           N       0.00      0.00      0.00         8
           O       0.08      0.10      0.09        10
           P       0.00      0.00      0.00         8
           Q       0.00  